In [108]:
import requests
import re
import json
from tqdm.auto import tqdm
from collections import defaultdict
import pickle 
import pandas as pd
import pymorphy2
import time

from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
import nltk

from sklearn.metrics.pairwise import linear_kernel

In [121]:
#скачиваем с api вакансии
sber = '3529'
page = 1
num_per_page = 100
ekaterinburg = 1261

url = f'https://api.hh.ru/vacancies?employer_id={sber}&page={page}&per_page={num_per_page}&area={ekaterinburg}'
res = requests.get(url)
vacancies = res.json()
if vacancies is None:
        time.sleep(600)
        
# извлекаем требование и описание
all_vacancy_ids = []
for i in tqdm(range(vacancies.get('pages'))):
    num_pages = vacancies.get('pages')
    vacancy_id = [el.get('id') for el in vacancies.get('items')]
    all_vacancy_ids.extend(vacancy_id)
     
df = pd.DataFrame(all_vacancy_ids)
df

  0%|          | 0/3 [00:00<?, ?it/s]

0
0    47785508
1    47999781
2    48860696
3    47999741
4    48802151
..        ...
295  47961037
296  48478993
297  47855645
298  47761533
299  48075495

[300 rows x 1 columns]

In [161]:
all_vacs= {}
all_vacids = all_vacancy_ids


for vacid in tqdm(all_vacids):
    url = f'https://api.hh.ru/vacancies/{vacid}?host=hh.ru'
    paramz = {
            'employer_id':sber,
            'per_page':num_per_page,
            'area': ekaterinburg,
        }
    res = requests.get(url, params=paramz)
    all_vacs[vacid]= res.json()

  0%|          | 0/300 [00:00<?, ?it/s]

In [162]:
all_vacs

{'47785508': {'id': '47785508',
  'premium': False,
  'billing_type': {'id': 'standard', 'name': 'Стандарт'},
  'relations': [],
  'name': 'Клиентский менеджер',
  'insider_interview': None,
  'response_letter_required': False,
  'area': {'id': '1304',
   'name': 'Сысерть',
   'url': 'https://api.hh.ru/areas/1304?host=hh.ru'},
  'salary': {'from': 45200, 'to': None, 'currency': 'RUR', 'gross': True},
  'type': {'id': 'open', 'name': 'Открытая'},
  'address': None,
  'allow_messages': True,
  'site': {'id': 'hh', 'name': 'hh.ru'},
  'experience': {'id': 'noExperience', 'name': 'Нет опыта'},
  'schedule': {'id': 'fullDay', 'name': 'Полный день'},
  'employment': {'id': 'full', 'name': 'Полная занятость'},
  'department': {'id': '3529-3529-stat', 'name': 'Сбер. Начало карьеры'},
  'contacts': None,
  'description': '<p><strong>Клиентский менеджер</strong></p> <p> </p> <p>Клиентский менеджер ― специалист, который продает продукты Сбера в отделении банка через планшет и терминалы самообслуж

In [157]:
df = pd.json_normalize(all_vacs)
#df = all_vacs[['id','name','description','alternate_url']]
#list(df.columns.values) #список столбцов 
df

47785508.id  47785508.premium 47785508.billing_type.id  \
0    47785508             False                 standard   

  47785508.billing_type.name 47785508.relations        47785508.name  \
0                   Стандарт                 []  Клиентский менеджер   

  47785508.insider_interview  47785508.response_letter_required  \
0                       None                              False   

  47785508.area.id 47785508.area.name  ... 48075495.negotiations_url  \
0             1304            Сысерть  ...                      None   

   48075495.suitable_resumes_url  \
0                           None   

                        48075495.apply_alternate_url 48075495.has_test  \
0  https://hh.ru/applicant/vacancy_response?vacan...             False   

   48075495.test          48075495.alternate_url 48075495.working_days  \
0           None  https://hh.ru/vacancy/48075495                    []   

  48075495.working_time_intervals  48075495.working_time_modes  \
0                              []                           []   

  48075495.accept_temporary  
0                     False  

[1 rows x 6378 columns]

In [143]:
df_all.shape

(1, 4)

In [151]:
#скачиваем с api вакансии
sber = '3529'
page = 1
num_per_page = 100
ekaterinburg = 1261
url = f'https://api.hh.ru/vacancies?employer_id={sber}&page={page}&per_page={num_per_page}&area={ekaterinburg}'
res = requests.get(url)
vacancies = res.json()
if vacancies is None:
    time.sleep(600)
    
for i in tqdm(range(vacancies.get('pages'))):
    num_pages = vacancies.get('pages')
    res = requests.get(url)
    vacancies_all = res.json()
    df = pd.json_normalize(vacancies_all,record_path='items')
    df = df[['id','name','snippet.responsibility','alternate_url']]
    df

  0%|          | 0/3 [00:00<?, ?it/s]

In [149]:
#list(df1.columns.values)      список столбцов 
df = pd.json_normalize(vacancies_all,record_path='items')
df = df[['id','name','snippet.responsibility','alternate_url']]
df

id                                               name  \
0   47785508                                Клиентский менеджер   
1   47999781    Старший менеджер по обслуживанию (с. Кировград)   
2   47999741       Старший менеджер по обслуживанию (с. Кашино)   
3   48802151             QA Automation Engineer (Телемаркетинг)   
4   48860696                                        IT-рекрутер   
..       ...                                                ...   
95  47961037                   Старший менеджер по обслуживанию   
96  48478993                                      Data engineer   
97  47855645  Старший менеджер по обслуживанию (с. Нейво-Руд...   
98  47761533  Старший менеджер по обслуживанию (Покровск-Ура...   
99  47839929    Старший менеджер по обслуживанию (п. Лопатково)   

                               snippet.responsibility  \
0   Продавать продукты банка и экосистемы физическ...   
1   Осуществлять операции по обслуживанию физическ...   
2   Осуществлять операции по обслуживанию физическ...   
3   Актуализация текущего фреймворка. Разработка а...   
4   Наша задача - выстроить доверительные отношени...   
..                                                ...   
95  Осуществлять операции по обслуживанию физическ...   
96  Разработка функциональных и интеграционных мод...   
97  Осуществлять операции по обслуживанию физическ...   
98  Осуществлять операции по обслуживанию физическ...   
99  Осуществлять операции по обслуживанию физическ...   

                     alternate_url  
0   https://hh.ru/vacancy/47785508  
1   https://hh.ru/vacancy/47999781  
2   https://hh.ru/vacancy/47999741  
3   https://hh.ru/vacancy/48802151  
4   https://hh.ru/vacancy/48860696  
..                             ...  
95  https://hh.ru/vacancy/47961037  
96  https://hh.ru/vacancy/48478993  
97  https://hh.ru/vacancy/47855645  
98  https://hh.ru/vacancy/47761533  
99  https://hh.ru/vacancy/47839929  

[100 rows x 4 columns]

In [152]:
df.shape

(100, 4)

In [52]:
#предобрабатываем и добавляем преобразованный текст в новый столбец 'text_clean'
#удаляем пропуски
df.dropna(subset = ['snippet.responsibility'], inplace = True)

In [53]:
# функция удаления пунктуации и цифр
def remove_trash(list): 
    pattern = '[^А-Яа-я0-9]+'
    try:
      list = [re.sub(pattern, ' ', i) for i in list] 
      print (list)
    except Exception as e:
      print(e)
    return list
df['text_clean'] = remove_trash(df['snippet.responsibility'])

# функция удаления html-тэгов
def remove_trash(list): 
    pattern = r'<.*?>'
    try:
      list = [re.sub(pattern, ' ', i) for i in list] 
      print (list)
    except Exception as e:
      print(e)
    return list
df['text_clean'] = remove_trash(df['snippet.responsibility'])

['Наша задача выстроить доверительные отношения с нанимающими менеджерами для оптимальных сроков укомплектования штата и выполнения планов по закрытию ', 'Осуществлять операции по обслуживанию физических лиц Проводить кассовые операции прием выдача обмен денег ', 'Актуализация текущего фреймворка Разработка автотестов Поддержка автотестов Заведение дефектов ', 'Поддержка генерации и отбора идей оценка трудоемкости Декомпозиция и анализ задач бэклога Проектирование решения в том числе разработка детальной внутренней ', 'Осуществлять операции по обслуживанию физических лиц Проводить кассовые операции прием выдача обмен денег ', 'Осуществлять операции по обслуживанию физических лиц Проводить кассовые операции прием выдача обмен денег ', ' разработка новых приложений Поддержание развитие существующих приложений Кодревью Написание тестов Участие в обсуждении и проектировании архитектуры и бизнес логики ', 'Осуществлять операции по обслуживанию физических лиц Проводить кассовые операции прие

In [54]:
# функция лемматизации - приводит в 1 форму
morph = pymorphy2.MorphAnalyzer()
def lemmatize(row):
    t = []
    text = row['text_clean']
    for word in text.split():
        if len(word)<=3:   #удаляет слова, которые меньше == 3 символа
            continue
        p = morph.parse(word)[0]
        t.append(p.normal_form)
    return " ".join(t)
df['text_clean'] = df.apply(lemmatize,axis=1)

In [55]:
#удалить часто встречающиеся слова и стоп-слова
stop_russian = stopwords.words('russian')

#текст преобразуем в векторное представление
text_transformer = TfidfVectorizer(stop_words=stop_russian, ngram_range=(1,1), lowercase=True, max_features=15000 )
text = text_transformer.fit_transform(df['text_clean'])

In [56]:
#что ищем
text_to_find = 'Звонить существующим клиентам и предлагать продукты'

In [57]:
#создали матрицу по поиску
text_to_find_matrix = text_transformer.transform([text_to_find])

# расчет косинусного расстояния
cosine_similarities = linear_kernel(text, text_to_find_matrix).flatten()

# запишем все попарные результаты сравнений
df['cos_similarities'] = cosine_similarities
# и отсортируем по убыванию (т.к. cos(0)=1)
df = df.sort_values(by=['cos_similarities'], ascending=[0])

# Выведем 3 самых близких результата
for index, row in df[0:3].iterrows():
    print(row['id'], row['snippet.responsibility'], row['cos_similarities'], )

48038299 Мы – новая команда Управления ИТ «Кредитные продукты» розничного бизнеса, которая занимается проектированием и разработкой витрин данных для создания финансовой отчётности. -  0.21534365472868938
48174845 готов помогать клиентам в решении повседневных задач, связанных с банковскими продуктами и услугами. Задачи: - предлагать банковские продукты и услуги по... 0.16685508034211063
48110655 Мобильное приложение, которое позволяет клиенту банка самостоятельно провести осмотр и сделать фотографии того имущества, которое клиент предлагает банку в залог... 0.14267821886794826


In [ ]:
df